## Model with polynomial features

In [1]:
#pip install scikit-learn==0.23.2

In [2]:
#import library

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import LinearRegression, Ridge, RidgeCV, Lasso, LassoCV, ElasticNet, ElasticNetCV
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, OneHotEncoder, PolynomialFeatures
from sklearn import metrics

In [3]:
#Columns to be considered

num_col = {'Bsmt Cond',
 'Bsmt Exposure',
 'Bsmt Qual',
 'BsmtFin SF 1',
 'Exter Cond',
 'Exter Qual',
 'Fireplaces',
 'Full Bath',
 'Garage Cars',
 'Garage Cond',
 'Garage Qual',
 'Gr Liv Area',
 'Heating QC',
 'Kitchen Qual',
 'Mas Vnr Area',
 'Open Porch SF',
 'Overall Qual',
 'Total_area',
 'Wood Deck SF',
 'age_since_built',
 'lot_frontage_imputed'}

cat_to_num = {'Exter Qual', 'Exter Cond', 'Bsmt Qual', 'Bsmt Cond',
    'Bsmt Exposure', 'Heating QC',
    'Kitchen Qual', 'Garage Qual', 'Garage Cond'}
     


cat_col = {'Bldg Type',
 'Foundation',
 'Street',
 'Central Air',
 'Electrical',
 'MS Zoning',
 'Land Contour',
 'Mas Vnr Type',
 'Heating',
 'Paved Drive',
 'Neighborhood'
          }

In [4]:
def cleaning_data(df):
    
    # 1. Drop most missing columns 
    df = df.drop(
    columns=['Pool QC', 'Misc Feature', 'Alley', 'Fence', 'Fireplace Qu'])

    # 2. Impute lot frontage
    from sklearn.linear_model import LinearRegression
    X_lot = df[df['Lot Frontage'] > 0][['1st Flr SF','Lot Area']]
    y_lot = df[df['Lot Frontage'] > 0]['Lot Frontage']
    lot_model = LinearRegression()
    lot_model.fit(X_lot,y_lot)
    
    lot_frontage_imputed = []
    for i in range(len(df)):
        if df.loc[i,'Lot Frontage'] > 0:
            lot_frontage_imputed.append(df.loc[i,'Lot Frontage'])
        else:
            lot_frontage_imputed.append(lot_model.predict([df.loc[i,['1st Flr SF','Lot Area']]])[0])

    df['lot_frontage_imputed'] = lot_frontage_imputed
    df = df.drop(columns = ['Lot Frontage'])
    
    #Garage Imputation

    df['Garage Yr Blt'] = df['Garage Yr Blt'].map(lambda x: x if x > 0 else 0)
    df['Garage Finish'] = df['Garage Finish'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Qual'] = df['Garage Qual'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Cond'] = df['Garage Cond'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Type'] = df['Garage Type'].map(lambda x: x if type(x) == str else 'NO')
    
    #Basement imputation
    df['Bsmt Exposure'] = df['Bsmt Exposure'].map(lambda x: x if type(x) == str else 'NO')
    df['BsmtFin Type 1'] = df['BsmtFin Type 1'].map(lambda x: x if type(x) == str else 'NO')
    df['BsmtFin Type 2'] = df['BsmtFin Type 2'].map(lambda x: x if type(x) == str else 'NO')
    df['Bsmt Cond'] = df['Bsmt Cond'].map(lambda x: x if type(x) == str else 'NO')
    df['Bsmt Qual'] = df['Bsmt Qual'].map(lambda x: x if type(x) == str else 'NO')
    
    #Mansory type and area
    df['Mas Vnr Type'] = df['Mas Vnr Type'].map(lambda x: x if type(x) == str else 'NO')
    df['Mas Vnr Area'] = df['Mas Vnr Area'].map(lambda x: x if x > 0 else 0)
    
    #Electrical Imputation
    df['Electrical'] = df['Electrical'].map(lambda x: x if type(x) == str else df['Electrical'].mode()[0])
    #Drop other observation containing Null
    df = df.dropna()
    
    return df

#Feature Engieering Function
def feat_eng(df):
    df['age_since_built'] = df['Yr Sold'] - df['Year Built']
    df['Total_area'] = df['Total Bsmt SF'] + df['1st Flr SF'] + df['2nd Flr SF']
    return df
#Converted OrdiNal Categorical columns to Numerical 
def cat2num(df):
    for col in cat_to_num:
        df[col] = df[col].map(to_num)
    return df

#Conversion function
def to_num(val):
    if val == 'Ex':
        return 5
    elif val == 'Gd':
        return 4
    elif val == 'TA' or val == 'Av':
        return 3
    elif val == 'Fa' or val == 'Mn':
        return 2
    elif val == 'Po' or val == 'No':
        return 1
    elif val == 'NO':
        return 0



In [5]:
def prep(df, train_df):
    """
    df = DataFrame to be transformed
    train_df = cleaned training set
    """

    #OneHotEncoding
    encoder = OneHotEncoder(handle_unknown='ignore', sparse=False)
    encoder.fit(train_df[cat_col])
    df_encode = pd.DataFrame(encoder.transform(df[cat_col]),
                             columns=encoder.get_feature_names(
                                 df[cat_col].columns),
                             index=df.index)

    train_df_encode = pd.DataFrame(encoder.transform(train_df[cat_col]),
                                   columns=encoder.get_feature_names(
                                       train_df[cat_col].columns),
                                   index=train_df.index)

    #Applying Polynomial Features
    poly = PolynomialFeatures(degree=2, include_bias=False)
    df_withpoly = pd.DataFrame(
        poly.fit_transform(df[num_col]),
        columns=poly.get_feature_names(input_features=df[num_col].columns),
        index=df.index)

    train_df_withpoly = pd.DataFrame(
        poly.fit_transform(train_df[num_col]),
        columns=poly.get_feature_names(
            input_features=train_df[num_col].columns),
        index=train_df.index)

    #Merge with numerical attribute
    X_new = pd.concat([df_withpoly, df_encode], axis=1)
    X_train = pd.concat([train_df_withpoly, train_df_encode], axis=1)

    #Standardize
    ss = StandardScaler()
    ss.fit(X_train)

    X_new_scaled = ss.transform(X_new)

    return X_new


#     return X_new_scaled

Preprocessing order
1. Cleaning
1. Feature engineering
1. cat_to_num
1. OneHotEncoding

In [6]:
train = pd.read_csv('../datasets/train.csv')
train = cleaning_data(train)
train = feat_eng(train)
train = cat2num(train)
X_train = prep(train,train)
y_train = train['SalePrice']

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  return f(*args, **kwargs)
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  return f(*args, **kwargs)
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Pleas

In [7]:
test = pd.read_csv('../datasets/test.csv')
test = cleaning_data(test)
test = feat_eng(test)
test = cat2num(test)
X_test = prep(test,train)

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  return f(*args, **kwargs)
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  return f(*args, **kwargs)
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Pleas

## Model Training

### Instantiate

In [8]:
#MLR
lr = LinearRegression()

#Ridge LR
r_alphas = np.logspace(0, 5, 100)
ridge_cv = RidgeCV(alphas=r_alphas,cv=5)

#Lasso LR
l_alphas = np.arange(0.001, 1, 0.01)
lasso_cv = LassoCV(alphas=l_alphas, max_iter=5000,cv=5)

#Elasticnet LR
l1_ratio = np.linspace(0, 1, 11)
enet_cv = ElasticNetCV(alphas=l_alphas, l1_ratio=l1_ratio, max_iter=5000,cv=5)

### Training

In [ ]:
#MLR Fitting
lr.fit(X_train,y_train)

#RidgeLR Fitting
ridge_cv.fit(X_train,y_train)

#LassoLR Fitting
lasso_cv.fit(X_train,y_train)

#ElasticNetLR Fitting
enet_cv.fit(X_train,y_train)

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 297914339122.77484, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 296019105462.02734, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 295512699516.72314, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/pytho

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 295215669838.29694, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 295210289500.33044, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 295206707608.0524, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294987433136.8076, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294987435186.9732, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294963472844.52167, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294838612198.58344, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294834137078.216, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294831187101.7409, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294747167210.48444, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294743303209.37317, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 294739457523.74164, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/pytho

...

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 332978160596.29486, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 332904150655.85406, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 332829419186.0521, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 330782369580.6898, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 330684613860.07916, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 330585677660.5584, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 327775533770.296, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 327635977471.2005, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 327494181586.58325, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 323193490721.4563, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 322963649892.3068, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 322728249477.3514, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 314314466845.75653, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 313762304817.14417, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:526: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 313180095272.84625, tolerance: 1000280150.7726442
  model = cd_fast.enet_coordinate_descent_gram(


In [ ]:
#RMSE on training set
print('Linear Regression')
print(metrics.mean_squared_error(y_train,lr.predict(X_train),squared = False),'\n')
print('Ridge Regression')
print(metrics.mean_squared_error(y_train,ridge_cv.predict(X_train),squared = False),'\n')
print('Lasso Regression')
print(metrics.mean_squared_error(y_train,lasso_cv.predict(X_train),squared = False),'\n')
print('ElasticNet Regression')
print(metrics.mean_squared_error(y_train,enet_cv.predict(X_train),squared = False),'\n')

### Cross Validation

In [ ]:
ridge = Ridge(alpha=ridge_cv.alpha_,max_iter=5000)
lasso = Lasso(alpha=lasso_cv.alpha_,max_iter=5000)
enet = ElasticNet(alpha=enet_cv.alpha_, l1_ratio=enet_cv.l1_ratio_,max_iter=5000)

#Cross Validation RMSE
lr_cv_score = cross_val_score(
    lr, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
ridge_cv_score = cross_val_score(
    ridge, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
lasso_cv_score = cross_val_score(
    lasso, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
enet_cv_score = cross_val_score(
    enet, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1

In [ ]:
#Cross Validation RMSE
print('Linear Regression')
print(lr_cv_score,'\n')
print('Ridge Regression')
print(ridge_cv_score,'\n')
print('Lasso Regression')
print(lasso_cv_score,'\n')
print('ElasticNet Regression')
print(enet_cv_score,'\n')

the Best model ranked by cross validation score is ElasticNet Regression

### Save model for later us

Since the ElasticNet model is the best option I have, I'll save and continue to develop on this model

In [ ]:
from joblib import dump, load
dump(enet, 'enet_regressor.joblib') 

## Baseline score

Establishing a baseline rmse by predicting mean for every observation

In [ ]:
res = y_train - np.mean(y_train)
mse = np.sum(np.power(res,2)/len(y_train))
rmse = np.sqrt(mse)

In [ ]:
rmse

Our model perform far better than the baseline RMSE

### Making prediction and submit the result!

In [ ]:
enet.fit(X_train,y_train)
Polynomial_prediction = enet.predict(X_test)
Polynomial_submission = pd.DataFrame(Polynomial_prediction,
                                   index=test.Id,
                                   columns=['SalePrice'])
Polynomial_submission.to_csv('../Submission/Polynomial_submission.csv')